# CASFM Uncertainty Vizualizations

In [1]:
import pandas as pd
import numpy as np

# Import figure from bokeh.plotting
from bokeh.io import show, output_notebook, output_file
from bokeh.plotting import figure

## Import profile data

In [79]:
# Read in the CSV file: df
df = pd.read_csv('results_q.csv', header=None)

# Correct header to show average discharge
# iterate over relevant rows
i = 4

# iterate over relevant columns
for j in range(10,510):
    # append average discharge of reach, after converting to 1 decimal
    cfs_float = float(df.iloc[0,j])
    df.iloc[i,j]= np.round(cfs_float,decimals=0)
    
# Append statistic columns and average discharges to column names
for j in range(0,510):
    df.rename(columns={j:df.iloc[i,j]}, inplace=True)

# drop the first 4 rows, drop columns with all NaN values
df = df.iloc[5:]
df = df.dropna(axis=1, how='all')

# rearrange the dataframe with q values ascending, statistic columns in place
stats_columns = list(df.columns.values[0:10])
value_columns = list(df.columns.values[10:])
value_columns = sorted(value_columns)
reorder_columns = stats_columns + value_columns
df = df[reorder_columns]

df.head(10)

XS   DIFF      MAX     AVERAGE      MIN  STDEV   99th PCT   90thPCT  \
5   24915.69  13.73  6603.74   6598.5025  6590.01  2.043  6602.5205  6601.021   
6   24750.84   6.79  6591.74   6588.7855  6584.95  1.206  6590.9004  6590.251   
7   24494.04   7.21  6581.11  6578.14286   6573.9  1.209  6580.3306  6579.503   
8   24361.28   5.82  6570.15  6567.78162  6564.33  0.992  6569.4404  6568.832   
9   24241.61   5.55  6562.44  6559.81938  6556.89  0.903  6561.5708  6560.902   
10  24084.46   7.69  6556.88  6553.15896  6549.19  1.301  6555.6014  6554.702   
11  23948.67   9.46  6551.48  6546.88774  6542.02  1.613  6549.9714  6548.816   
12  23791.52   8.84  6540.27   6536.0081  6531.43  1.476  6538.8512  6537.765   
13  23592.79   8.03  6530.05  6526.47352  6522.02  1.399  6528.9308  6527.981   
14  23394.54   9.29  6521.96  6517.61538  6512.67  1.639   6520.691  6519.614   

    10th PCT    1st PCT   ...      6629.0   6673.0   6693.0   6890.0   7080.0  \
5    6596.13    6592.33   ...      6602.1  6602.13  6602.15  6602.37  6602.52   
6   6587.238    6585.12   ...     6590.84  6590.86  6590.87   6590.9   6590.9   
7   6576.569    6574.19   ...     6580.28  6580.31  6580.29  6580.32  6580.33   
8   6566.468    6564.54   ...     6569.28  6569.36  6569.38  6569.42  6569.44   
9   6558.649    6557.11   ...     6561.52  6561.55  6561.56  6561.56  6561.57   
10  6551.438  6549.3799   ...     6555.51  6555.57  6555.56   6555.6   6555.6   
11  6544.786     6542.3   ...     6549.88  6549.93  6549.93  6549.96  6549.97   
12  6534.107    6531.68   ...     6538.73   6538.8  6538.81  6538.84  6538.85   
13  6524.438    6522.26   ...      6528.8  6528.87  6528.86   6528.9  6528.93   
14  6515.414    6512.96   ...     6520.56  6520.56  6520.63  6520.65  6520.69   

     7222.0   7274.0   7581.0   8381.0   8968.0  
5   6602.57  6602.57  6602.82   6603.6  6603.74  
6   6590.96  6590.94  6591.05  6591.26  6591.74  
7   6580.39  6580.46  6580.48  6580.68  6581.11  
8   6569.48  6569.53  6569.57  6569.75  6570.15  
9   6561.65  6561.69  6561.76  6561.86  6562.44  
10  6555.76  6555.85  6555.74   6556.2  6556.88  
11  6550.11  6550.23  6550.28  6550.67  6551.48  
12  6538.97  6539.07  6539.13  6539.47  6540.27  
13  6529.01  6529.11  6529.04  6529.42  6530.05  
14  6520.79  6520.88  6520.89  6521.28  6521.96  

[10 rows x 516 columns]

## Define percentiles

In [3]:
# Define the percentile ranges of interest
q_percentiles = [10,25,75,90]
q_vals = (df.columns.values[10:])
q_percentile_vals = np.percentile(q_vals, q_percentiles)
q_percentile_vals

# Find the median of the q values

# If dataset is even in length, drop the last entry to avoid averaging middle two values
if np.remainder(len(q_vals), 2) == 0:
    q_vals = q_vals[:-1]

q_median = np.median(q_vals)
print ('median of q_vals: ', q_median)

median of q_vals:  3757.0


## Define colors for plots

In [20]:
# For 4 breaks (5 bins) in the percentiles plus 1 extra for median water surface
colors = ['red', 'orange', 'blue', 'orange', 'red', 'yellow']

## Define function for profile plot

In [21]:
# Define function for creating profile plot
def uncertainty_profile_plot(ws_dataframe, x_axis_label, y_axis_label):
    # Create the figure: p
    p = figure(x_axis_label=x_axis_label, y_axis_label=y_axis_label, width=800)
    
    # Create water surface line plot
    for j in range(10,510):
        if df.columns[j] < q_percentile_vals[0]:
            p.line(df['XS'], df[df.columns[j]], alpha=0.35, color=colors[0])
        elif q_percentile_vals[0] < df.columns[j] < q_percentile_vals[1]:
            p.line(df['XS'], df[df.columns[j]], alpha=0.35, color=colors[1])
        elif q_percentile_vals[1] < df.columns[j] < q_percentile_vals[2]:
            p.line(df['XS'], df[df.columns[j]], alpha=0.35, color=colors[2])
        elif q_percentile_vals[2] < df.columns[j] < q_percentile_vals[3]:
            p.line(df['XS'], df[df.columns[j]], alpha=0.35, color=colors[3])
        else:
            p.line(df['XS'], df[df.columns[j]], alpha=0.35, color=colors[4])

        # Plot the mode q value
        if df.columns[j] == q_median:
            p.line(df['XS'], df[df.columns[j]], color=colors[5], line_width=5)

    # Create ground surface line plot
    x=[0,25000]
    y=6400
    p.line(x, y, color='black')
    
    output_notebook()
    # output_file('test.html')
    show(p)

## Create profile plot

In [22]:
uncertainty_profile_plot(df,'river_station', 'ws')

Loading BokehJS ...

## Import cross section data

In [95]:
# Import xs data from hec-ras' profile plot, copy values to clipboard option
df_xs = pd.read_csv('XS.csv', header=1)


df_xs_cols = df_xs.columns.values

for j in range(len(df_xs_cols)):
    label1 = df_xs[df_xs.columns[j]].iloc[0]
    label2 = df_xs_cols[j]
    label3 = label2 + '_' + label1

    # Append x,y labels to existing columns headers
    df_xs.rename(columns={label2:label3}, inplace=True)  

# Drop the first row now that its appended to the column headers
df_xs = df_xs.iloc[1:,:]

# Convert to numeric from string
df_xs[['Label.1_x', 'Ground_y']] = df_xs[['Label.1_x','Ground_y']].apply(pd.to_numeric)

df_xs.head()

Label_x Unnamed: 1_y  Label.1_x     Ground_y    Label.2_x   Bank Sta_y  \
1           99  6598.619141       0.00  6612.310059  137.7200012  6590.700195   
2           99         6610       1.98  6610.890137          NaN          NaN   
3          127         6610       2.96  6610.180176  159.7700043  6590.720215   
4          127  6594.631836       3.95  6609.470215          NaN          NaN   
5  126.8700027  6594.680176       4.94  6608.770020          NaN          NaN   

     Label.3_x WS CWCB-100yr_y  
1          127     6598.532715  
2  187.9481049     6598.532715  
3          NaN             NaN  
4  148.8000031     6598.532715  
5          NaN             NaN

## Define function for cross section plot

In [133]:
# Define function for creating cross section plot
def uncertainty_xs_plot(xs_dataframe, x_axis_label, y_axis_label):
    # Create the figure: p
    p = figure(x_axis_label=x_axis_label, y_axis_label=y_axis_label, width=800)
    
    # Define extents of cross section's x values
    x_min = np.min(xs_dataframe['Label.1_x'])
    x_max = np.max(xs_dataframe['Label.1_x'])
    y_min = np.min(xs_dataframe['Ground_y'])

    # Create water surface line plots
    for j in range(10,510):
        # Define x,y pairs for xs water surfaces (flat water)
        x_vals = [x_min, x_max]
        y_vals = [df.iloc[0,j], df.iloc[0,j]]

        if df.columns[j] < q_percentile_vals[0]:
            p.line(x_vals, y_vals, alpha=0.35, color=colors[0])
        elif q_percentile_vals[0] < df.columns[j] < q_percentile_vals[1]:
            p.line(x_vals, y_vals, alpha=0.35, color=colors[1])
        elif q_percentile_vals[1] < df.columns[j] < q_percentile_vals[2]:
            p.line(x_vals, y_vals, alpha=0.35, color=colors[2])
        elif q_percentile_vals[2] < df.columns[j] < q_percentile_vals[3]:
            p.line(x_vals, y_vals, alpha=0.35, color=colors[3])
        else:
            p.line(x_vals, y_vals, alpha=0.35, color=colors[4])

        # Plot the mode q value
        if df.columns[j] == q_median:
            p.line(x_vals, y_vals, color=colors[5], line_width=5)

    # Create ground surface glyph plot
    
    # Add two additional x,y pairs to allow for path glyph to fill under ground rather than over
    ground_x = [x_min] + list(df_xs['Label.1_x']) + [x_max]
    ground_y = [(y_min - 5)] + list(df_xs['Ground_y']) + [(y_min - 5)] 
    p.patch(ground_x, ground_y, color='lightgray', alpha=0.8)
    
    # Create structure glyph plot
    p.patch(df_xs['Label_x'] ,df_xs['Unnamed: 1_y'], color='gray', alpha=0.8)
    
    output_notebook()
    # output_file('test.html')
    show(p)

In [135]:
uncertainty_xs_plot(df_xs, 'XS 24750 station', 'Elevation')

Loading BokehJS ...

In [6]:
# References:
# Embedding Bokeh Server in Jupyter: http://biobits.org/bokeh-jupyter-embed.html
# https://github.com/ecerami/pydata-essentials/blob/master/bokeh/data/iris.data